# BEM For Helmholtz Sound-Soft Scattering Problem Using NGSolve

We fix the notation that we will use from now on in this report, let $\Omega_{-}\subset \mathbb{R}^2$ be a bounded Liptschiz domain and $\Omega_{+}$ the complement of its closure in $\mathbb{R}^2$. We require $\Omega_{-}$ to be simply connected.
Let us recall the Helmholtz PDE, that is gonna be the focus of our report:
$$\Delta u  + k^2 u=0$$
\begin{definition}[Radiating Helmholtz Solution]We will say that a function $u\in H^{1}_{loc}(\mathbb{R}^2\backslash B_R)$ is a radiating Helmholtz solution if for a given $k\in \mathbb{R}$:
$$
    \Delta u + k^2 u=0 \;\forall x \in \mathbb{R}^2\backslash B_R
$$ and $|\partial_r u - iku|=o(r^{-\frac{1}{2}})$ for $r\to \infty$.
\end{definition}

\begin{definition}[Exterior Dirichlet Problem]
Given  $k\in\mathbb{N}$ and a function $g \in H^{\frac{1}{2}}(\partial\Omega_{-})$ we say that a function $u\in H^1_{loc}(\overline{\Omega_{+}})$ is solution to the Exterior Dirichlet Problem associated with $k$ and $g$ if,
\begin{equation}
\Delta u + k^2 u = 0 \; in \; \Omega_{+}\\
\gamma^{+}u = g \;on\; \partial\Omega_{-}\\
u \; is \; radiating
\end{equation}
where $\gamma^{+}$ is the trace operator from $H^1(\Omega_{+})\to H^{\frac{1}{2}}(\partial\Omega_{+})$, that is defined on $C^1(\overline{\Omega_{+}})$ and then extended by density.
\end{definition}

Last we introduce the definition of Sound-Soft scattering problem that is gonna be the problem we aim to solve numerically and analytically in this report.
\begin{definition}
Given a function $u_{In}$ that is a radiating Helmholtz solution on $\partial\Omega_{-}$ we say that $u_{ST}\in H^{1}_{loc}(\overline{\Omega_{+}})$ is a solution to the sound soft scattering problem (SSSP) if:
\begin{equation}
    \Delta u_{ST} + k^2 u_{ST} = 0\; in \; \Omega_{+}\\
    \gamma^{+}(u_{ST}+u_{IN})=0 \; on \; \Gamma\\
    u_{ST}\; is \; radiating
\end{equation}
\end{definition}

The focus of this report will be to study the SSSP problems both analytically and numerically, in particular using a collocation BEM method using as computational toolbox the Netgen/NGSolve python interface [more info](https://ngsolve.org/). First of all we have to import all the library related to the Netgen/NGSolve environment, we also imported some elements from the native math library, numpy and matplotlib. Last but not least we import NGSolve special_functions library that has to be compiled separtely and extend all the SLATEC functions as CoefficientFunctions [more info](https://github.com/NGSolve/ngs-special-functions).

In [ ]:
from ngsolve import *
#import netgen.gui
import netgen.meshing as ms
import ngsolve.special_functions as sp
from netgen.geom2d import SplineGeometry
from math import pi
import numpy as np
import matplotlib.pyplot as plt
from ngsolve.webgui import Draw

### Example - SSSP and Circular Scatterer
We wont to consider a sound soft scattering problem where $\Omega$ is a circle of radius $\frac{1}{4}$ centered in the origin and $u_{In}$ is a planar wave defined as
$$ u_{in}(\vec{x}) = e^{i(\vec{x}\cdot \vec{d})}, \;\; \vec{d}=\Big(\frac{1}{2},\frac{\sqrt{3}}{2}\Big)$$
In the following code we first define the geometry using Netgen 2D Geometry package and the we draw the planner wave $u_{In}$.

In [ ]:
#(-1,1)------(1,1)
#   |          |
#   |          |     
#(-1,-1)----.(1,-1)
geo = SplineGeometry()
geo.AddRectangle((1,1),(-1,-1),bc="rectangle")


########################
#  CIRUCLAR SCATTERER  #
#######################
N = 40;
pnts=[];
for i in range(0,N):
    pnts.append((0.25*cos(2*(i/N)*pi),0.25*sin(2*(i/N)*pi)))
    pnts.append((0.25*cos(2*(i/N)*pi+(pi/N)),0.25*sin(2*(i/N)*pi+(pi/N))))

#pnts.append((0.25*cos(2*(0/N)*pi),0.25*sin(2*(0/N)*pi)))

P = [geo.AppendPoint(*pnt) for pnt in pnts]
Curves = [[["spline3",P[i-1],P[i],P[i+1]],"c"+str(int((i-1)/2))] for i in range(1,2*N-1,2)]
Curves.append([["spline3",P[2*N-2],P[2*N-1],P[0]],"c"+str(N-1)])
[geo.Append(c,bc=bc) for c,bc in Curves]
mesh = Mesh(geo.GenerateMesh(maxh=0.1))
rho = sqrt(x**2+y**2);
theta = atan2(y,x)
Draw(theta,mesh,'theta')
k = 30;
lam = 1;

def PW(Angle):
    pw = exp(1j*k*sqrt(x**2+y**2)*sqrt((0.5*sqrt(3))**2+0.25)*cos(theta-Angle));
    return pw;
Uin = IfPos(rho-0.25,PW(pi/6),0)
Draw(Uin,mesh,'Uin',min=-1,max=1.0,autoscale=False)

Now we study a preliminary case, we assume $u_{In}$ to be a circular harmonic on $\partial \Omega_{+}$, i.e. $\gamma_{+}u_{In}(\theta) = e^{il\theta}$ for a fixed $l\in \mathbb{Z}$. In this case a solution of the SSSP is given by a convex combination of $\frac{H_l^{(j)}(kr)}{H_l^{(j)}(kR)}e^{il\theta}$, $j=1,2$. This because $\frac{H_l^{(j)}(kr)}{H_l^{(j)}(kR)}e^{il\theta}$ verify the Helmholtz equation and therefore as well any linear combination of the above mentioned term verify the Helmholtz equation. Furthermore on $\partial\Omega{+}$ we have that $u_{In}+u_{St}$ is equal to:
$$ e^{il\theta} - \lambda\frac{H_l^{(1)}(kR)}{H_l^{(1)}(kR)}e^{il\theta} -(1-\lambda) \frac{H_l^{(2)}(kR)}{H_l^{(2)}(kR)}e^{il\theta} = e^{il\theta}-e^{il\theta}=0$$
Therefore we know that for a circular harmonic the solution has the form:
$$u_{St}(\rho,\theta) = -\lambda\frac{H_l^{(1)}(k\rho)}{H_l^{(1)}(kR)}e^{il\theta} -(1-\lambda) \frac{H_l^{(2)}(k\rho)}{H_l^{(2)}(kR)}e^{il\theta}$$
we still have to meet the requirement that $u_{St}$ is a radiating Helmholtz solution, we expand the Henkel functions for a large argument as:
$$H_l^{(j)}(z) = \sqrt{\frac{2}{\pi z}} e^{i(-1)^{j+1}(z-\frac{l\pi}{2}-\frac{\pi}{4})}$$
    that only $-\lambda\frac{H_l^{(1)}(k\rho)}{H_l^{(1)}(kR)}e^{il\theta}$ is the radiating components and therefore we take $\lambda=1$.
Now since we the Helmholtz equation is linear, such as the Dirichlet boundary condition and the radiating condition we can state that if we can decompose the $u_{In}$ in the sum of circular harmonic, ie. $u_{In}(\rho,\theta) = \sum_{l\in \mathbb{Z}} a_l(\rho) e^{il\theta}$, we have a solution of the SSSP given by:
$$\label{eq:HankelSolution}u_{St}(\rho,\theta) = \sum_{l\in \mathbb{Z}} -a_l(\rho)\frac{H_l^{(1)}(k\rho)}{H_l^{(1)}(kR)}e^{il\theta}$$

Let's us consider a planar wave that propagates in the direction $(1,0)$ and that has wave number $k=3$, we can write its equation as:
$$u(\vec{x}) = e^{ik(\vec{d}\cdot\vec{x})}$$
we can rewrite the above equation in polar coordinates as follow:
$$u(\rho,\theta) = e^{ik\rho\cos(\theta)}$$
now we can put to good use the Jacobi-Anger expansion, i.e. $e^{i\rho\cos(\theta)} = J_0(\rho)+2\sum^{\infty}_{l=1} J_l(\rho)\cos(l\theta)$, to obtain:
$$u(\rho,\theta) = J_0(k\rho)+2\sum^{\infty}_{l=1} J_l(k\rho)\cos(l\theta)$$
the usual form of the Jacobi-Anger is expansion is $e^{iz\cos(\theta)} = \sum^{\infty}_{l =-\infty} J_l(z)e^{il\theta}$, but using the identity $J_{-l}(z) = (-1)^l J_l(z)$ we can write it the form above. We use this representation because negative index Hankel function presents some problem when wrapped from SLATEC in NGSolve special functions.
We now use the NGSolve toolbox to see if the series representation of $u_{In}$ is some how accurate, we then use equation \eqref{eq:HankelSolution} to compute an approximation of $u_{St}$ and $u_{tot} = u_{In}+u_{St}$.

In [ ]:
def MieSeriesPW(Angle):
    u = sp.jv(z=k*sqrt(x**2+y**2)*sqrt((0.5*sqrt(3))**2+0.25), v=0);
    for l in range(1,50):
        t = (1j**l)*(sp.jv(z=k*sqrt(x**2+y**2)*sqrt((0.5*sqrt(3))**2+0.25), v=l))*cos(l*(theta-Angle));
        u = u+2*t;
    return u;
UMie = IfPos(rho-0.25,MieSeriesPW(pi/6),0)
Draw(UMie,mesh,'UMie',min=-1,max=1,autoscale=False)
print("L2 error of Mie-Series rappresentation: ",abs(Integrate((UMie-Uin)**2,mesh)))

In [ ]:
def MieSerieST(Angle):
    h = sp.hankel1(z=k*sqrt(x**2+y**2),v=0)/sp.hankel1(z=k*0.25,v=0);
    u = -1*sp.jv(z=k*0.25, v=0)*h;
    for l in range(1,50):
        h = sp.hankel1(z=k*sqrt(x**2+y**2),v=l)/sp.hankel1(z=k*0.25,v=l);
        t = -2*(1j**l)*(sp.jv(z=k*0.25, v=l))*cos(l*(theta-Angle))*h;
        u = u+t;
    return u;
Ust = IfPos(rho-0.25,MieSerieST(pi/6),0)
Draw(Ust,mesh,'Ust',min=-1,max=1,autoscale=False)
Utot = Uin+Ust;
Draw(Utot,mesh,'Utot',min=-1,max=1,autoscale=False)

## Collocation BEM
In this section we focus on the SSSP where $\Omega_{-}$ is a generic polygon, in particular choose as $\Omega_{-}$ a triangle which has barycenter in the origin. First we have to define the geometry of the problem using Netgen 2D Geometry library. 

In [ ]:
#(-1,1)------(1,1)
#   |          |
#   |          |     
#(-1,-1)----.(1,-1)
geo = SplineGeometry()
geo.AddRectangle((1,1),(-1,-1),bc="rectangle")
########################
#  TRIANGLE SCATTERER  #
########################
gamma = 0.6;
def l(x):
    return -x+1;
M = 10;


pnts=[];
for i in range(0,M+1):
    pnts.append((0,i/M));
for i in range(1,M):
    pnts.append((i/M,l(i/M)))
for i in range(0,M):
    pnts.append(((M-i)/M,0));
plt.scatter([p[0] for p in pnts],[p[1] for p in pnts])
TPnts = [(gamma*(p[0]-(1/3)),gamma*(p[1]-(1/3)))for p in pnts]
P = [geo.AppendPoint(*pnt) for pnt in TPnts]  

Curves = [[["line",P[i],P[i+1]],"l"+str(int(i))] for i in range(0,len(pnts)-1)]
Curves.append([["line",P[len(pnts)-1],P[0]],"l"+str(int(len(pnts)-1))])

#[geo.Append(c,bc=bc) for c,bc in Curves]
#print(Curves)


pnts2=[];
for j in range(0,3*M):
    if j in range(0,M):
        plt.plot(pnts[j][0],pnts[j][1]+(0.5/M),'r*');
        pnts2.append((pnts[j][0],pnts[j][1]+(0.5/M)));
    elif j in range(2*M,3*M):
        plt.plot(pnts[j][0]-(0.5/M),pnts[j][1],'y*');
        pnts2.append((pnts[j][0]-(0.5/M),pnts[j][1]));
    else:
        plt.plot(pnts[j][0]+(0.5/M),pnts[j][1]-(0.5/M),'g*');
        pnts2.append((pnts[j][0]+(0.5/M),pnts[j][1]-(0.5/M)))
        
TPnts2 = [(gamma*(p[0]-(1/3)),gamma*(p[1]-(1/3)))for p in pnts2]

P2 = [geo.AppendPoint(*pnt) for pnt in TPnts2]  

 
#print(len(pnts),len(pnts2))
Curves = []
for i in range(0,len(pnts)-1):
    Curves.append([["line",P[i],P2[i]],"m"+str(2*int(i+1)-1)])
    Curves.append([["line",P2[i],P[i+1]],"m"+str(2*int(i+1))])
Curves.append([["line",P[len(pnts)-1],P2[len(pnts)-1]],"m"+str(2*(len(pnts2))-1)])
Curves.append([["line",P2[len(pnts)-1],P[0]],"m"+str(2*(len(pnts2)))])
#print(Curves)

[geo.Append(c,bc=bc) for c,bc in Curves]


mesh = Mesh(geo.GenerateMesh(maxh=0.025))

rho = sqrt(x**2+y**2);
theta = atan2(y,x)
Draw(theta,mesh,'theta')

To do this we introduce the Helmholtz fundamental solution:
$$
\Phi_k(\vec{x},\vec{y}) = \frac{i}{4} H_0^1(|\vec{x}-\vec{y}|),\qquad\qquad \forall \vec{x},\vec{y} \in \mathbb{R}^2 \; such\; that\;\vec{x}\ne \vec{y} .$$
Any linear combination of the form $\sum_{j} \psi_j \Phi_k(\cdot,\vec{y_j})$, where $\vec{y_j}\in\overline{\Omega_{-}}$, is a radiating Helmholtz solution in $\Omega_{+}$. We can take a continuous linear combination, focused on $\vec{y_j}\in \partial \Omega_{-}$, to obtain a radiating Helmholtz solution:
$$\mathcal{S}\psi (\vec{x}) = \int_{\partial\Omega_{-}} \psi(\vec{y})\Phi_k(\vec{x},\vec{y})ds(\vec{y})\qquad\qquad \vec{x}\in \Omega_{+}$$
the operator $\mathcal{S}$ is called Helmholtz single layer potential.
We similarly define the single layer operator as follow:
$$\mathcal{S}\psi (\vec{x}) = \int_{\partial\Omega_{-}} \psi(\vec{y})\Phi_k(\vec{x},\vec{y})ds(\vec{y})\qquad\qquad \vec{x}\in \partial\Omega_{-}$$

In [ ]:
N = 3*M;
A = np.zeros((N,N),complex)
F = np.zeros((N,1),complex)
j=10
HelmholtzSLP = CoefficientFunction(0.25*1j*sp.hankel1(z=k*sqrt((TPnts2[j][0]-x)**2+(TPnts2[j][1]-y)**2),v=0))
#Draw(HelmholtzSLP,mesh,"SLP")

tol = 10e-4

for j in range(0,N):
    #print(Integrate(1,mesh,definedon=mesh.Boundaries("c"+str(i))))
    for i in range(0,N):
        HelmholtzSLP = CoefficientFunction(0.25*1j*sp.hankel1(z=k*sqrt((TPnts2[j][0]-x)**2+(TPnts2[j][1]-y)**2),v=0))
        A[i,j]= Integrate(HelmholtzSLP,mesh,definedon=mesh.Boundaries("m"+str(2*(i+1)-1)))+Integrate(HelmholtzSLP,mesh,definedon=mesh.Boundaries("m"+str(2*(i+1)))); 
        mip = mesh(TPnts2[j][0],TPnts2[j][1]);
    F[j] = PW(pi/3)(mip);
print(np.linalg.cond(A))
#print(F)
Psi = np.linalg.solve(A,F)
#print(Psi)
def SLP(Psi):
    u = 0;
    for j in range(0,N):
        #HelmholtzSLP = CoefficientFunction(0.25*1j*sp.hankel1(z=k*sqrt((TPnts[j][0]-x)**2+(TPnts[j][1]-y)**2),v=0))
        if j in range(0,M):
            h=1/M;
            HelmholtzSLP = CoefficientFunction(0.25*1j*sp.hankel1(z=k*sqrt((TPnts2[j][0]-x)**2+(TPnts2[j][1]-y)**2),v=0))
        elif j in range(2*M,N):
            h=1/M;
            HelmholtzSLP = CoefficientFunction(0.25*1j*sp.hankel1(z=k*sqrt((TPnts2[j][0]-x)**2+(TPnts2[j][1]-y)**2),v=0))
        else:
            #sqrt(2) is due to path integral
            h = (1/M)
            HelmholtzSLP = CoefficientFunction(0.25*1j*sp.hankel1(z=k*sqrt((TPnts2[j][0]-x)**2+(TPnts2[j][1]-y)**2),v=0))
        u -= h*Psi[j][0]*HelmholtzSLP;
    return u;


Ust = SLP(Psi)
Uin = PW(pi/3)
Utot = Ust+Uin;
Draw(Uin,mesh,'Uin',min=-1,max=1,autoscale=False)
Draw(Ust,mesh,'Ust',min=-1,max=1,autoscale=False)
Draw(Utot,mesh,'Utot',min=-1,max=1,autoscale=False)